In [1]:
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)
import random
import numpy as np
import matplotlib.pyplot as plt
from importlib import reload
import subprocess

import mido
import IPython.display as ipd
import pretty_midi
from visual_midi import Plotter
from visual_midi import Preset

import scales as scales
from generator import generator

In [3]:
warnings.filterwarnings("ignore", category=DeprecationWarning)
tpb = 480  # ticks per beat
sd = 0.16  # standard deviation of the duration and velocity
rp = 0.24  # rest probability
mid = mido.MidiFile(ticks_per_beat=tpb)

tempo = mido.bpm2tempo(140) # tempo beats per minute
# Create a separate track (track 0) for tempo changes
tempo_track = mido.MidiTrack()
mid.tracks.append(tempo_track)
tempo_track.append(mido.MetaMessage('set_tempo', tempo=tempo))

song_name = 'test'

track_list = ['bass_1', 'bass_2', 'melody_1', 'melody_2', 'melody_3']
comb = {c: {} for c in track_list}
# Define scales for each track
scale_list = [scales.minor_pentatonic['notes'], scales.minor_pentatonic['notes'],
              scales.minor_pentatonic['notes'], scales.minor_11_arpeggio['notes'], 
              scales.minor_9_arpeggio['notes']]
# Define pitch, octave, and duration weights for each track, or leave as None to use default
pitch_weights = [[2,1,1,1.5,1], [2,1,1,1.5,1], None, None, None]
octave_weights = [[1,1,2,1,0,0,0,0,0], [0,1,2,1,1,0,0,0,0], 
                  [0,0,0,1,2,1,1,0,0], [0,0,0,0,0,1,1,1,1], [0,0,0,1,1,2,1,0,0]]
duration_weights = [[0,0,0,1,2,1,1,1], [0,0,0,1,2,1,1,1], 
                    [1,1,1,1,1,1,1,1], [1,1,2,1,1,1,0,0], [0,1,2,1,1,1,0,0]]
sequence_lengths = [100, 100, 120, 400, 400]    # need longer lengths for tracks playing short notes
sd = [0.16, 0.16, 0.16, 0.16, 0.16]       # sd of the duration and velocity (proportion of mean)
rp = [0.24, 0.24, 0.24, 0.24, 0.24]       # rest probability

# add pitch and octave weights to comb dict
for i,c in enumerate(comb):
    comb[c]["scale"] = scale_list[i]
    comb[c]['pitch_weights'] = pitch_weights[i]
    comb[c]['octave_weights'] = octave_weights[i]
    comb[c]['duration_weights'] = duration_weights[i]
    comb[c]["length"] = sequence_lengths[i]
    comb[c]['sd'] = sd[i]
    comb[c]['rp'] = rp[i]

for i, c in enumerate(comb.values()):
    track = mido.MidiTrack()
    mid.tracks.append(track)
    track.name = track_list[i] # assign the track name
    sequence, midi_notes = generator(c["scale"], pitch_weights=c['pitch_weights'],
                                    octave_weights=c['octave_weights'], duration_weights=c['duration_weights'],
                                     length=c["length"], tpb=tpb, 
                                     duration='fixed', velocity='variable',
                                     sd=c['sd'], rest_probability=c['rp'])
    # Add the note events to the MIDI track
    for note in midi_notes:
        track.append(note)

# Write the MIDI file to disk
midi_path = f'generated/{song_name}_tracks_{len(comb)}.mid'
mid.save(midi_path)
# Load the MIDI file using pretty_midi
midi_data = pretty_midi.PrettyMIDI(midi_path)
# Plot the MIDI data
preset = Preset(plot_width=850, plot_height=600)
plotter = Plotter(preset, plot_max_length_bar=16)
plotter.show_notebook(midi_data)
# Synthesize the MIDI file into a waveform
audio_data = midi_data.synthesize(fs=44100)
# Normalize the audio data
audio_data /= np.max(np.abs(audio_data))
# Play the audio data in the Jupyter notebook
ipd.Audio(audio_data, rate=44100)

# # optional - open in GarageBand or DAW of choice
# subprocess.call(['open', '-a', 'GarageBand', midi_path])

Loading BokehJS ...